In [1]:
import pandas as pd
import numpy as np
from scipy.interpolate import griddata
from scipy.interpolate.interpolate import interp1d
import plotly.graph_objects as go

In [2]:
class DataHandler:
    def __init__(self, spinner=False, blades=3):
        self.spinner = 's' if spinner else ''
        self.blades = blades
        self.load_data()

    def filename(self):
        return r'\clark_{}{}_{}.csv'.format(self.blades, self.spinner, self.chart)
    
    def load_data(self):
        data = pd.read_csv(r'data\large_angles' + self.filename(), engine='python')
        data = data.melt(id_vars = ['x'], var_name = 'y', value_name = 'z').dropna()
        data.y = data.y.astype(float)
        self.data = data.reset_index(drop=True)
        
    def save_data(self):
        df_pivot = self.curves.pivot(index='y', columns='x', values='z')
        df_pivot = df_pivot.iloc[::-1].fillna(value=0, limit=2).iloc[::-1]
        df = pd.melt(df_pivot.reset_index(), id_vars='y', value_vars=df_pivot.columns, value_name = 'z')
        self.curves = df[['x', 'y', 'z']].dropna().reset_index(drop=True).sort_values(by=['x', 'y'])
        self.curves.to_csv(r'data\mesh' + self.filename(), index=False)
              
    def appendTo(self, df, x, y, z):
        return df.append(pd.DataFrame({'x': x, 'y': y, 'z': z}), ignore_index=True)
        
    def interpolate(self, points, mesh, z):
        x = interp1d(points.z, points.x, kind = 'quadratic', fill_value='extrapolate')
        y = interp1d(points.z, points.y, kind = 'quadratic', fill_value='extrapolate')
        mesh = mesh.append({'x': float(x(z)), 
                            'y': float(y(z)), 
                            'z': z}, ignore_index=True)
        return mesh
        
        

In [3]:
class Propeller(DataHandler):
        
    def create_mesh(self):
        if self.chart == 'eff':
            self.densing(y_vals=[10])
            self.meshing()
            self.extrapolated_data()
            self.create_data()
            self.densing(y_vals=self.y_vals())
            self.meshing()
        else:
            self.meshing()
            self.densing()
            self.extrapolated_data()
            self.create_data()
            self.meshing()
            self.mesh_add_x()
            self.densing()
        
    def meshing(self):
        pass
        
    def densing(self):
        pass
    
    def create_curves(self):
        pass
    
    def plot_data(self, df, color, name, size=3):
        return go.Scatter3d(
            x=df.x, y=df.y, z=df.z,
            mode='markers',
            marker=dict(size=size, color=color, opacity=0.9),
            name=name)
    
    def layout(self):
        camera = dict(eye=dict(x=1.3, y=-1.3, z=0.5),
                      center=dict(y=-0.1, z=-0.15))
        scene = dict(
            xaxis = dict(title='J'),
            yaxis = dict(title='Angle'),
            zaxis = dict(title='Eff' if self.chart=='eff' else 'Cp')
        )
        legend = dict(font = {'size': 12}, itemsizing = 'trace')
        return go.Layout(margin=dict(l=0, r=0, b=0, t=0), 
                         width=1024, height=768, 
                         scene=scene,
                         scene_camera=camera,
                         legend_title_text='Data',
                         legend=legend)
    
    def draw(self, y_max=60):
        df = self.data[self.data.y <= y_max]
        fig = go.Figure(layout = self.layout())
        fig.add_trace(self.plot_data(df, 'black', 'NACA', 2 if self.chart=='eff' else 3))
        if hasattr(self, 'extra') and self.data.min().y == 15:
            fig.add_trace(self.plot_data(self.extra, 'gray', 'New', 4))
        if hasattr(self, 'mesh'):
            df = self.mesh[self.mesh.y <= y_max]
            fig.add_trace(self.plot_data(df, 'red', 'Sides'))
        if hasattr(self, 'top'):
            df = self.top[self.top.y <= y_max]
            fig.add_trace(self.plot_data(df, 'green', 'Top'))
        fig.show()
        
    def draw_curves(self, y_max=60, top=True):
        df = self.curves[self.curves.y <= y_max].reset_index(drop=True)
        fig = go.Figure(layout = self.layout())
        fig.add_trace(self.plot_data(df, 'black', 'Siatka', 2))
        if top:
            df = self.top[self.top.y <= y_max].reset_index(drop=True)
            fig.add_trace(self.plot_data(df, 'green', 'Góra'))
        fig.show()

    def draw_surface(self):
        data = self.curves.drop_duplicates(subset=['x', 'y'])
        data = data.pivot(index='y', columns='x', values='z')
        fig = go.Figure(go.Surface(
            z=data.values,
            x=data.columns,
            y=data.index,
            showscale=False,
            colorscale='algae',
            opacity=0.9,
            reversescale=True,
            hovertemplate=
            '<b>J</b>: %{x}<br>' +
            '<b>Angle</b>: %{y}°<br>' +
            '<b>{}</b>: '.format(self.chart.capitalize()) +
            '%{z}<extra></extra>',
        ), layout = self.layout())
        fig.show()
        
    def fit(self):
        fig = go.Figure(layout=go.Layout(margin=dict(l=20, r=20, b=0, t=0), width=240, height=480, showlegend=False))
        points = self.top[self.top.y==10]
        fig.add_trace(go.Scatter(x=points.x, 
                                 y=points.z, 
                                 mode='markers', 
                                 marker=dict(size=5, color='green')))
        if self.chart == 'cp':
            point = self.mesh[self.mesh.y==10]
            fig.add_trace(go.Scatter(x=point.x, 
                                     y=point.z, 
                                     mode='markers', 
                                     marker=dict(size=5, color='red')))
            fig.update_layout(width=480, height=240)
        data = self.data[self.data.y==10]
        fig.add_trace(go.Scatter(x=data.x, 
                                 y=data.z, 
                                 line=dict(color='black')))
        if self.chart == 'eff':
            fig.update_yaxes(range=[-0.02, 0.8])
        fig.update_xaxes(title='J')
        fig.update_yaxes(title=self.chart.capitalize())
        fig.show()
    
    def x_vals(self, begin=0, end=4.8, dense=False):
        vals = np.linspace(0, 5, 5001) if dense else np.linspace(0, 5, 51)
        vals = np.round(vals, 3)
        return vals[ (vals >= begin) & (vals <= end) ]
    
    def y_vals(self, begin=10):
        vals = np.linspace(10, 60, 101) if self.chart == 'eff' else np.linspace(10, 60, 51)
        vals = np.round(vals, 2)
        return vals[vals >= begin]
        
    def create_data(self):
        points = self.extra[self.extra.y == 10]
        z = interp1d(points.x, points.z, kind='quadratic')
        x = self.x_vals(dense=True, end=points.x.max())
        x = np.append(x, points.x.max())
        self.data = self.appendTo(self.data, x, 10, z(x))
    
    

In [4]:
class Cp(Propeller):
    chart = 'cp'
    
    def densing(self):
        top = pd.DataFrame()
        extrapolate = False if hasattr(self, 'top') else True
        x_vals = [0, 0.3] if extrapolate else self.x_vals(end=3.2)
        df = self.data.append(self.mesh, ignore_index=True)
        for x in x_vals:
            inters = df[df.x == x]
            y_vals = self.y_vals(begin=10 if extrapolate else inters.y.min())
            kind = 'linear' if extrapolate else 'quadratic'
            z = interp1d(inters.y, inters.z, kind=kind, fill_value='extrapolate')
            top = self.appendTo(top, x, y_vals, z(y_vals))
        self.top = top
        
    def mesh_add_x(self):
        x_vals = self.x_vals(begin=self.mesh.x.min(), end=3.2)
        y = interp1d(self.mesh.x, self.mesh.y, kind='quadratic')
        self.mesh = self.appendTo(self.mesh, x_vals, y(x_vals), 0)
        
    def plane_intercepts(self, z):
        inters = pd.DataFrame()
        for y in self.data.y.unique():
            df = self.data[(self.data.y == y) & (self.data.z < 0.2)]
            inters = self.interpolate(df, inters, z)
        return inters
     
    def meshing(self) -> pd.DataFrame:
        inters = self.plane_intercepts(0)
        y_vals = self.y_vals()
        x = interp1d(inters.y, inters.x, kind='quadratic', fill_value='extrapolate')
        self.mesh = pd.DataFrame({'x': x(y_vals), 'y': y_vals, 'z': 0})
        
    def extrapolated_data(self):
        self.extra = self.mesh.append(self.top, ignore_index=True)
        
    def create_curves(self, append=False):
        curves = pd.DataFrame()
        df = self.top.append(self.mesh, ignore_index=True)
        mesh_x = self.mesh[self.mesh.y.isin(self.y_vals())].x
        x_vals = np.linspace(0, mesh_x[0], 10, endpoint=False)
        x_vals = np.append(x_vals, mesh_x)
        for y in prop.y_vals(begin=10):
            inters = df[df.y == y]
            z = interp1d(inters.x, inters.z, kind='quadratic')
            x = x_vals[x_vals <= inters.x.max()]
            curves = self.appendTo(curves, x, y, z(x))
        self.curves = curves.round({'x': 3, 'z': 4}).drop_duplicates(subset=['x', 'y'])

In [5]:
class Efficiency(Propeller):
    chart = 'eff'
        
    def create_curves(self):
        curves = pd.DataFrame()
        bottom_x = self.top[(self.top.z == 0) & (self.top.x > 0)].reset_index(drop=True).x
        x_vals = np.linspace(0, 1, 10, endpoint=False)**0.4*bottom_x[0]
        x_vals = np.append(x_vals, bottom_x)
        for y in prop.y_vals(begin=10):
            inters = self.top[self.top.y == y]
            z = interp1d(inters.x, inters.z, kind='quadratic')
            x = x_vals[x_vals <= inters.x.max()]
            curves = self.appendTo(curves, x, y, z(x))
        self.curves = curves.round({'x': 3, 'z': 4}).drop_duplicates(subset=['x', 'y'])
        
    def densing(self, y_vals):
        """Ratio-based top mesh"""
        mesh = pd.DataFrame()
        z_left = np.linspace(0, 0.99, 10)**0.2 if self.blades == 2 else np.linspace(0, 0.99, 30)**0.7
        z_right = np.linspace(0, 0.99, 5)**0.2 if self.blades == 2 else np.linspace(0, 1, 30)**0.5
        if hasattr(self, 'top'):
            z_left = np.linspace(0, 0.99, 20)**0.7
            z_right = np.linspace(0, 1, 15)**0.4
        for z_rel in z_left:
            points = self.top_intercepts(z_rel, side='left')
            mesh = self.interpolate_y(points, mesh, y_vals)
        for z_rel in z_right:
            points = self.top_intercepts(z_rel, side='right')
            mesh = self.interpolate_y(points, mesh, y_vals)
        self.top = mesh
        
    def interpolate_y(self, points, mesh, y_vals):
        """Get the interpolated x and z values at y_vals"""
        kind = 'linear' if self.blades == 2 and not hasattr(self, 'top') else 'quadratic'
        x = interp1d(points.y, points.x, kind=kind, fill_value='extrapolate')
        z = interp1d(points.y, points.z, kind='quadratic', fill_value='extrapolate')
        return self.appendTo(mesh, x(y_vals), y_vals, z(y_vals))
    
    def meshing(self, extrapolate):
        pass
    
    def top_intercepts(self, relative_z, side):
        '''Points intercepting at the same relative z for every curve'''
        points = pd.DataFrame()
        for y in self.data.y.unique():
            df = self.data[self.data.y == y]
            topX = df.at[df.z.idxmax(), 'x']
            if relative_z == 1:
                points = points.append(df.loc[df.z.idxmax()])
            else:
                curve = df[df.x > topX + 0.03] if side == 'right' else df[df.x < topX - 0.03]
                points = self.interpolate(curve, points, df.z.max() * relative_z)
        return points
        
    def extrapolated_data(self):
        if self.blades == 2:
            '''Top data'''
            self.top.loc[self.top.y==10, 'x'] *= 1.1
            self.extra = self.top
        else:
            '''Polynomial fit approach'''
            points = self.top[self.top.y==10]
            begin = 0.2 if self.blades == 3 else 0.25
            x_vals = np.arange(begin, points.max().x + 0.02, 0.001)
            p, ssr, rank, sv, ct = np.polyfit(points.x, points.z, deg=5, full=True)
            print(round(ssr[0], 5))
            z = np.poly1d(p)
            extra = pd.DataFrame({'x': x_vals, 'y': 10, 'z': z(x_vals)})
            extra = extra.append({'x': 0, 'y': 10, 'z': 0}, ignore_index=True)
            self.extra = extra[extra.z >= 0]
    
    

In [8]:
prop = Efficiency(blades=4)
# prop.create_mesh()
self = prop
self.densing(y_vals=[10])
self.extrapolated_data()
self.create_data()
prop.fit()
self.densing(y_vals=self.y_vals())
prop.draw(y_max=60)


0.09854


In [7]:
prop = Cp(spinner=False, blades=3)
# prop.create_mesh()
self = prop
self.meshing()
self.densing()
self.extrapolated_data()
self.create_data()
prop.fit()
self.meshing()
self.mesh_add_x()
self.densing()

prop.draw(y_max=60)

In [9]:
prop.create_curves()
prop.draw_curves(y_max=60, top=False)
prop.save_data()

In [10]:
prop.draw_curves(y_max=60, top=False)

In [12]:
prop.draw_surface()

In [ ]:
class EfficiencyOld(Propeller):
    chart = 'eff'
    
    def z_vals(self, dense):
        density = 15 if dense else 4
        end = self.data.max().z
        end *= 0.9 if dense else 0.75
        return np.linspace(0, end, density)
        
    def create_mesh(self):
        self.densing(idx_deltas=[-40, 10], y_vals=[10])
        self.meshing(y_vals=[10], dense=False)
        self.extrapolated_data()
        self.create_data()
        self.densing(idx_deltas=[-50, -20, 0, 20, 50], y_vals=self.y_vals(begin=10))
        self.meshing(y_vals=self.y_vals(begin=10))
        
    def densing(self, y_vals, idx_deltas):
        """Index-based top mesh, not recommended"""
        top = pd.DataFrame()
        df = self.data
        for i in idx_deltas:
            idx = [df[df.y == y].z.idxmax() + i for y in df.y.unique()]
            maxes = df[df.index.isin(idx)]
            x = interp1d(maxes.y, maxes.x, kind = 'quadratic', fill_value='extrapolate')
            z = interp1d(maxes.y, maxes.z, kind = 'quadratic', fill_value='extrapolate')
            top = self.appendTo(top, x(y_vals), y_vals, z(y_vals))
        cutoff = self.data.max().z * 0.5
        self.top = top[top.z > cutoff].reset_index(drop=True)
    
    def plane_intercepts(self, z, side='right'):
        inters = pd.DataFrame()
        for y in self.data.y.unique():
            df = self.data[self.data.y == y]
            topX = df.at[df.z.idxmax(), 'x']
            tail = df[df.x > topX + 0.1] if side == 'right' else df[df.x < topX - 0.1]
            if z < df.max().z:
                inters = self.interpolate(tail, inters, z)
        return inters
    
    def meshing(self, y_vals, dense=True) -> pd.DataFrame:
        mesh = pd.DataFrame()
        for z in self.z_vals(dense):
            inters_r = self.plane_intercepts(z)
            x_r = interp1d(inters_r.y, inters_r.x, kind='quadratic', fill_value='extrapolate')
            mesh = self.appendTo(mesh, x_r(y_vals), y_vals, z)
            if not hasattr(self, 'mesh'):
                inters_l = self.plane_intercepts(z, side='left')
                x_l = interp1d(inters_l.y, inters_l.x, kind='quadratic', fill_value='extrapolate')
                mesh = self.appendTo(mesh, x_l(y_vals), y_vals, z)
        for y in y_vals:
            z_max = self.top[self.top.y == y].min().z - 0.02
            z_max = z_max - 0.04 if len(y_vals) == 1 else z_max
            points_above_top = mesh[(mesh.y == y) & (mesh.z > z_max)]
            mesh.drop(points_above_top.index, inplace=True)
        self.mesh = mesh
        
#     def extrapolated_data(self):
#         '''Sides and top data, unchanged'''
#         self.extra = self.mesh.append(self.top, ignore_index=True)
        
    def extrapolated_data(self):
        '''Middle points approach'''
        sides = self.mesh.copy()
        top = self.top.copy()
        sidesMiddle = sides[sides.z == sides.max().z].x.mean()
        topMiddle = top[top.z == top.max().z].x.values[0]
        middle = (sidesMiddle + topMiddle) /2
        sides.x *= middle / sidesMiddle
        top.x *= middle / topMiddle
        self.extra = sides.append(top, ignore_index=True)
        
#     def extrapolated_data(self):
#         '''Polynomial fit approach'''
#         points = self.mesh.append(self.top, ignore_index=True)
#         x_vals = self.x_vals(end=points.max().x, dense=True)
#         p, ssr, rank, sv, ct = np.polyfit(points.x, points.z, 5, full=True)
#         print(round(ssr[0], 5))
#         z = np.poly1d(p)
#         self.extra = pd.DataFrame({'x': x_vals, 'y': 10, 'z': z(x_vals)})
        
    def create_curves(self):
        bottom = self.mesh[(self.mesh.z == 0) & (self.mesh.x > 0)]
        meshTop = self.mesh.append(self.top, ignore_index=True)
        curves = pd.DataFrame()
        smooth_10s = np.linspace(0.415, 0.715, 16)
        x_vals = np.sort(np.hstack((self.x_vals(), bottom.x.values, smooth_10s)))
        for y in prop.y_vals(begin=10):
            inters = meshTop[meshTop.y == y]
            z = interp1d(inters.x, inters.z, kind='quadratic', fill_value='extrapolate')
            x = x_vals[x_vals <= inters.x.max()]
            curves = self.appendTo(curves, x, y, z(x))
        self.curves = curves.round({'x': 3, 'z': 4}).drop_duplicates(subset=['x', 'y'])
    
    def fit(self):
        fig = go.Figure(layout=go.Layout(margin=dict(l=0, b=0, t=0), width=480, height=360))
        top = self.top[self.top.y==10]
        mesh = self.mesh[self.mesh.y==10]
        fig.add_trace(go.Scatter(x=top.x, y=top.z, mode='markers', 
                                 marker=dict(size=4, color='green'), name='top'))
        fig.add_trace(go.Scatter(x=mesh.x, y=mesh.z, mode='markers', 
                                 marker=dict(size=4, color='red'), name='sides'))
        fig.show()
    

In [ ]:
prop = EfficiencyOld(spinner=False, blades=2)
prop.create_mesh()
# self = prop
# self.densing(idx_deltas=[-50, 0, 50], y_vals=self.y_vals())
# self.meshing(y_vals=self.y_vals(), dense=False)
# self.extrapolated_data()
# self.create_data()
prop.fit()
prop.draw(y_max=50)

In [ ]:
data = prop.curves.drop_duplicates(subset=['x', 'y'])
data = data.pivot(index='y', columns='x', values='z')
data.iloc[-7:,-6:]

In [ ]:
np.linspace(0, 1, 51)**1.1*50+10